In [2]:
# Parameters
first_run = {"uid": 3, "simulationUid": 3, "name": "my runner", "description": "string", "createDate": 1656329488314, "trace": True, "dataSink": {"format": "JSON", "folderPath": "/Users/tiemokodembele/Documents/internShip/simulatte/data/ODM/loanvalidation", "uri": "/Users/tiemokodembele/Documents/internShip/simulatte/data/ODM/loanvalidation/run_my runner_20220627_133128.json", "username": "string", "password": "string", "uid": 9}, "decisionService": {"type": "ODM", "endPoint": "http://localhost:9060/DecisionService/rest/miniloan/1.0/Miniloan_ServiceRuleset", "authType": "NO_AUTH", "username": "string", "password": "string", "key": "string", "value": "string", "token": "string", "headerPrefix": "string", "uid": 6}, "executor": {"type": "JSE", "mode": "REMOTE", "capability": "ODM", "uid": 3}, "runReport": {"uid": 3, "status": "FINISHED", "numberOfDecisions": 5001, "numberOfRequests": 5001, "progress": 1.0, "duration": 29166, "numberOfDecisionsPerSecond": 171.46678}, "notebookUri": "/Users/tiemokodembele/Documents/internShip/simulatte/notebook/simulyticsOdm.ipynb"}
second_run = {"uid": 1, "simulationUid": 1, "name": "my runner", "description": "string", "createDate": 1656323493409, "trace": True, "dataSink": {"format": "JSON", "folderPath": "/Users/tiemokodembele/Documents/internShip/simulatte/data/ADS/loanvalidation", "uri": "/Users/tiemokodembele/Documents/internShip/simulatte/data/ADS/loanvalidation/run_my runner_20220627_115133.json", "username": "string", "password": "string", "uid": 3}, "decisionService": {"type": "ADS", "endPoint": "https://cpd-cp4a.apps.ads2201.cp.fyre.ibm.com/ads/runtime/api/v1/deploymentSpaces/embedded/decisions/_082392706%2Fbanking%2Fapproval_with_tasks%2FloanApprovalWithTasksDecisionService%2F1.1.0%2FloanApprovalWithTasksDecisionService-1.1.0.jar/operations/approvalWithTasks/execute", "authType": "ZEN_TOKEN", "username": "string", "password": "string", "key": "string", "value": "string", "token": "MDgyMjEzNzA2OjB6M3lwc29MZTJOOE1sQ2pDVDVSVXlmSHNXRDhDbjBKc1ZKZlN1aEI=", "headerPrefix": "string", "uid": 2}, "executor": {"type": "JSE", "mode": "REMOTE", "capability": "ODM", "uid": 1}, "runReport": {"uid": 1, "status": "FINISHED", "numberOfDecisions": 5000, "numberOfRequests": 5000, "progress": 1.0, "duration": 961437, "numberOfDecisionsPerSecond": 5.2005486}, "notebookUri": "/Users/tiemokodembele/Documents/internShip/simulatte/notebook/ads-vs-odm-loanvalidation-analytics.ipynb"}


__INSTALL DEPENDENCIES__

In [3]:
%%capture 

!pip install pgeocode
!pip install deepdiff

__LIBRAIRIES IMPORT__

In [4]:
import os
import sys

import requests
import random 

import pandas as pd 
import numpy as np
import json

__RUNS SPEC COMPARISON__ 

In [5]:
from deepdiff import DeepDiff
runs_diff = json.dumps(DeepDiff(first_run, 
                                second_run, 
                                exclude_paths={"root['uid']", 
                                                "root['name']", 
                                                "root['description']", 
                                                "root['createDate']", 
                                                "root['dataSink']", 
                                                "root['decisionService']['authType']", 
                                                "root['decisionService']['token']", 
                                                "root['decisionService']['uid']", 
                                                "root['executor']", 
                                                "root['runReport']['uid']"
                                                })['values_changed'], indent=4)

print(runs_diff)

{
    "root['simulationUid']": {
        "new_value": 1,
        "old_value": 3
    },
    "root['decisionService']['type']": {
        "new_value": "ADS",
        "old_value": "ODM"
    },
    "root['decisionService']['endPoint']": {
        "new_value": "https://cpd-cp4a.apps.ads2201.cp.fyre.ibm.com/ads/runtime/api/v1/deploymentSpaces/embedded/decisions/_082392706%2Fbanking%2Fapproval_with_tasks%2FloanApprovalWithTasksDecisionService%2F1.1.0%2FloanApprovalWithTasksDecisionService-1.1.0.jar/operations/approvalWithTasks/execute",
        "old_value": "http://localhost:9060/DecisionService/rest/miniloan/1.0/Miniloan_ServiceRuleset"
    },
    "root['runReport']['numberOfDecisions']": {
        "new_value": 5000,
        "old_value": 5001
    },
    "root['runReport']['numberOfRequests']": {
        "new_value": 5000,
        "old_value": 5001
    },
    "root['runReport']['duration']": {
        "new_value": 961437,
        "old_value": 29166
    },
    "root['runReport']['numberOfDecis

In [6]:
runs_diff_labels = ["Simulation uid", "Trace", "Decision service type", "Decision service endpoint", "Number of decisions", "Number of requests", "run duration", "Number of executed decision per second", "run metrics/KPI"]

__READ DECISION SINK__

In [22]:
# data sink uris
datasink_odm_path = first_run["dataSink"]["uri"]
datasink_ads_path = second_run["dataSink"]["uri"]

outputDataODM = []
outputDataADS = []

if os.path.exists(datasink_odm_path):
    with open(datasink_odm_path) as file:
        filesize = os.path.getsize(datasink_odm_path)
        if filesize == 0:
            print("The file {} is empty".format(datasink_odm_path))
        else:
            while (line := file.readline().rstrip()):
                jsonLine = dict()
                line_to_json = json.loads(line)
                jsonLine["request"] = json.loads(line_to_json["request"])
                if(line_to_json["trace"]=="empty"):
                    jsonLine["trace"] = "empty"
                else:
                    jsonLine["trace"] = json.loads(line_to_json["trace"])
                jsonLine["response"] = json.loads(line_to_json["response"])

                outputDataODM.append(jsonLine)

if os.path.exists(datasink_ads_path):
    with open(datasink_ads_path) as file:
        filesize = os.path.getsize(datasink_ads_path)
        if filesize == 0:
            print("The file {} is empty".format(datasink_ads_path))
        else:
            while (line := file.readline().rstrip()):
                jsonLine = dict()
                line_to_json = json.loads(line)
                jsonLine["request"] = json.loads(line_to_json["request"])
                if(line_to_json["trace"]=="empty"): 
                    jsonLine["trace"] = "empty" 
                else: 
                    jsonLine["trace"] = json.loads(line_to_json["trace"])
                jsonLine["response"] = json.loads(line_to_json["response"])

                outputDataADS.append(jsonLine)

datasink_odm = pd.json_normalize(outputDataODM)
datasink_ads = pd.json_normalize(outputDataADS)

datasink_odm.head(5)
datasink_ads.head(5)

   request.loan.duration  request.loan.amount  \
0                    223              1800775   
1                    145              1611454   
2                    262               819952   
3                    288               782883   
4                    235              1752316   

   request.loan.yearlyInterestRate  request.loan.yearlyRepayment  \
0                         0.044163                        142213   
1                         0.036699                        165310   
2                         0.039440                         56074   
3                         0.054162                         58354   
4                         0.034527                        123238   

   request.borrower.creditScore request.borrower.name  \
0                           322           Teresa Rice   
1                           427    Katherine Cummings   
2                           326        Abigail Wilson   
3                           448      Catherine Barnes   
4          

GET
- Total of approved amounts
- Total of requested amounts 
- f(yearlyIncome)=loanAmount

In [8]:
import plotly
from plotly.offline import plot, iplot, init_notebook_mode
init_notebook_mode(connected = True)

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import pgeocode

#Graph configs
approval_colors = ["#00CC96", "#FF6692"]
color_indices = [0, 1]

pie_chart_approval_loan_names = ['approved', 'rejected']
pie_chart_loan_amount_names = ['approved amount', 'rejected amount']
bidirectional_bar_chart_label_ads=['number of applications', 'sum of applications amounts']
bidirectional_bar_chart_label_odm=['number of applications', 'sum of applications amounts']
bidirectional_bar_chart_label=['number of rejected applications', 'sum of rejected applications amounts', 'number of approved applications', 'sum of approved applications amounts']
radar_chart_labels=['number of rejected applications', 'sum of rejected applications amounts', 'number of approved applications', 'sum of approved applications amounts', 'ratio approved/requested']

Metrics

In [9]:
########### ADS #############
select_approved_decision_ads = '`response.approved` == True'
select_rejected_decision_ads = '`response.approved` == False'

get_decision_approval_ads = 'response.approved'
get_decision_amount_ads = 'response.loan.amount'
get_decision_borrower_zipcode_ads = 'response.borrower.zipCode'
get_decision_borrower_yearly_income_ads = 'response.borrower.yearlyIncome'
get_decision_borrower_credit_score_ads = "response.borrower.creditScore"
get_decision_id_ads = 'response.__DecisionID__'
get_decision_reimboursement_ads = 'response.yearlyInterestRate'

########### ODM #############
select_approved_decision_odm = '`response.loan.approved` == True'
select_rejected_decision_odm = '`response.loan.approved` == False'

get_decision_approval_odm = 'response.loan.approved'
get_decision_amount_odm = 'response.loan.amount'
get_decision_borrower_yearly_income_odm = 'request.borrower.yearlyIncome'
get_decision_borrower_credit_score_odm = "request.borrower.creditScore"
get_decision_id_odm = 'response.__DecisionID__'
get_decision_reimboursement_odm = 'response.loan.yearlyInterestRate'


KPIs

In [10]:
########### ADS #############
approved_loan_ads = datasink_ads.query(select_approved_decision_ads)
rejected_loan_ads = datasink_ads.query(select_rejected_decision_ads)


########### ODM #############
approved_loan_odm = datasink_odm.query(select_approved_decision_odm)
rejected_loan_odm = datasink_odm.query(select_rejected_decision_odm)




########### Approved/Rejected PRINT #############
print("ADS : Number of approved loan request = ", approved_loan_ads.shape[0])
print("ADS : Number of rejected loan request = ", rejected_loan_ads.shape[0])
print("ADS : Rate of approval = ", approved_loan_ads.shape[0]/datasink_ads.shape[0])

print("ODM : Number of approved loan request = ", approved_loan_odm.shape[0])
print("ODM : Number of rejected loan request = ", rejected_loan_odm.shape[0])
print("ODM : Rate of approval = ", approved_loan_odm.shape[0]/datasink_odm.shape[0])


########### Approved/Rejected Amount PRINT #############
print("ADS : Total approved amount = ",datasink_ads.query(select_approved_decision_ads)[get_decision_amount_ads].sum())
print("ADS : Total rejected amount = ",datasink_ads.query(select_rejected_decision_ads)[get_decision_amount_ads].sum())
print("ADS : Total requested amount = ",datasink_ads[get_decision_amount_ads].sum())

print("ODM : Total approved amount = ",datasink_odm.query(select_approved_decision_odm)[get_decision_amount_odm].sum())
print("ODM : Total rejected amount = ",datasink_odm.query(select_rejected_decision_odm)[get_decision_amount_odm].sum())
print("ODM : Total requested amount = ",datasink_odm[get_decision_amount_odm].sum())

ADS : Number of approved loan request =  1051
ADS : Number of rejected loan request =  3949
ADS : Rate of approval =  0.2102
ODM : Number of approved loan request =  1124
ODM : Number of rejected loan request =  3877
ODM : Rate of approval =  0.22475504899020196
ADS : Total approved amount =  334108199
ADS : Total rejected amount =  4708644189
ADS : Total requested amount =  5042752388
ODM : Total approved amount =  380404912
ODM : Total rejected amount =  4615548637
ODM : Total requested amount =  4995953549


Visualization

__DONUT CHART__

In [11]:
########### settings ###########
donut_hole = 0.7

########### Approved/Rejected PIE CHART #############
trace_approval_ads = go.Pie(labels = pie_chart_approval_loan_names,
                            values = [approved_loan_ads.shape[0], rejected_loan_ads.shape[0]],
                            hole = donut_hole)
trace_approval_odm = go.Pie(labels = pie_chart_approval_loan_names,
                            values = [approved_loan_odm.shape[0], rejected_loan_odm.shape[0]],
                            hole = donut_hole)


########### Approved/Rejected Amount PIE CHART #############
trace_amount_ads = go.Pie(values=[datasink_ads.query(select_approved_decision_ads)[get_decision_amount_ads].sum(),
                                datasink_ads.query(select_rejected_decision_ads)[get_decision_amount_ads].sum()],
                            labels=pie_chart_loan_amount_names,
                            hole = donut_hole,
                            name="Loan amount ADS")
trace_amount_odm = go.Pie(values=[datasink_odm.query(select_approved_decision_odm)[get_decision_amount_odm].sum(),
                                datasink_odm.query(select_rejected_decision_odm)[get_decision_amount_odm].sum()],
                            labels=pie_chart_loan_amount_names,
                          hole = donut_hole,
                            name="Loan amount ODM")

fig = make_subplots(rows=2, cols=2,
                    specs=[[{"type": "pie"}, {"type": "pie"}],[{"type": "pie"}, {"type": "pie"}]],
                    column_widths=[0.5, 0.5],
                    #vertical_spacing=0.001,
                    subplot_titles=("ODM approval", "ADS approval", "ODM approved/rejected amount", "ADS approved/rejected amount")
                    )

fig.add_trace(trace_approval_odm, row=1, col=1)
fig.add_trace(trace_approval_ads, row=1, col=2)
fig.add_trace(trace_amount_odm, row=2, col=1)
fig.add_trace(trace_amount_ads, row=2, col=2)

fig.update_traces(hoverinfo='label', textinfo='value', textfont_size=15, textposition="outside",
                  marker=dict(colors=approval_colors, line=dict(color='#FFFFFF', width=7)))
                
fig.update_annotations(yshift=20) # subplot tiltes

fig.update_layout(
    barmode='stack',
    plot_bgcolor = "white",
    #paper_bgcolor = 'lightgray',
    height=800,
    title={'text': f"ODM vs ADS : 'number of applications' and 'sum of applications amounts'",
          'x':0.5,
          'y':0.98,
          'xanchor': 'center',
          'font_size': 20
    },
    annotations= [
         {
            "font": {
               "size": 15
            },
            "showarrow": False,
            "text": "<b>ODM</b><br>total amount<br> approved/rejected",
            "x": 0.22,
            "y": 0.11
         },
         {
            "font": {
               "size": 15
            },
            "showarrow": False,
            "text": "<b>ADS</b><br>total amount<br> approved/rejected",
            "x": 0.77,
            "y": 0.11
         },
         {
            "font": {
               "size": 15
            },
            "showarrow": False,
            "text": "<b>ODM</b> approval",
            "x": 0.23,
            "y": 0.76
         },
         {
            "font": {
               "size": 15
            },
            "showarrow": False,
            "text": "<b>ADS</b> approval",
            "x": 0.775,
            "y": 0.76
         }
      ]
    )

iplot(fig)

__SCATTER CHART__

In [12]:
def array_normalize(values, max_value=1):
    normalized_values = []
    for value in values:
        normalized_values.append((value*max_value)/max(values))
    return normalized_values

def set_colors(values, true_color="#00CC96", false_color="#FF6692"):
    colors = []
    for value in values:
        if(value): 
            colors.append(true_color) 
        else: 
            colors.append(false_color) 
    return colors

In [23]:
fig1 = go.Figure()
fig1.add_trace(go.Scatter(
                 x=datasink_odm[get_decision_borrower_yearly_income_odm],
                 y=datasink_odm[get_decision_amount_odm],
                 mode='markers',
                 marker_size=array_normalize(datasink_odm[get_decision_borrower_credit_score_odm], 20), 
                 marker_color=set_colors(datasink_odm[get_decision_approval_odm]),
                 text=datasink_ads[get_decision_approval_ads], 
                 hovertemplate="<b>Income:</b> %{x}<br><b>Loan amount:</b> %{y}<br><b>Approval:</b> %{text}<extra></extra>",
                 name='ODM'
))

fig1.add_trace(
    go.Scatter(
        x=np.array([0, max(datasink_odm[get_decision_borrower_yearly_income_odm])]),
        y=100*datasink_odm.query(select_approved_decision_odm)[get_decision_reimboursement_odm].mean()*np.array([0, max(datasink_odm[get_decision_borrower_yearly_income_odm])]),
        mode="lines",
        line=go.scatter.Line(color="#109618"),
        showlegend=False)
)
fig1.add_trace(
    go.Scatter(
        x=np.array([0, max(datasink_odm[get_decision_borrower_yearly_income_odm])]),
        y=max(datasink_odm.query(select_approved_decision_odm)[get_decision_amount_odm])*np.array([1, 1]),
        mode="lines",
        line=go.scatter.Line(color="#B82E2E"), ##B82E2E
        showlegend=False)
)


fig2 = go.Figure()
fig2.add_trace(go.Scatter(
                 x=datasink_odm[get_decision_borrower_yearly_income_odm],
                 y=datasink_odm[get_decision_amount_odm],
                 mode='markers',
                 marker_size=array_normalize(datasink_odm[get_decision_borrower_credit_score_odm], 20), 
                 marker_color=set_colors(datasink_odm[get_decision_approval_odm]),
                 text=datasink_ads[get_decision_approval_ads], 
                 hovertemplate="<b>Income:</b> %{x}<br><b>Loan amount:</b> %{y}<br><b>Approval:</b> %{text}<extra></extra>",
                 name='ODM'
))

fig2.add_trace(
    go.Scatter(
        x=np.array([0, max(datasink_ads[get_decision_borrower_yearly_income_ads])]),
        y=100*datasink_ads.query(select_approved_decision_ads)[get_decision_reimboursement_ads].mean()*np.array([0, max(datasink_ads[get_decision_borrower_yearly_income_ads])]),
        mode="lines",
        line=go.scatter.Line(color="#109618"),
        showlegend=False)
)
fig2.add_trace(
    go.Scatter(
        x=np.array([0, max(datasink_ads[get_decision_borrower_yearly_income_ads])]),
        y=max(datasink_ads.query(select_approved_decision_ads)[get_decision_amount_ads])*np.array([1, 1]),
        mode="lines",
        name='<b>Max amount</b> horizontal bar',
        line=go.scatter.Line(color="#B82E2E"), ##B82E2E
        showlegend=False)
)

"""
fig = make_subplots(rows=1, cols=2,
                    specs=[[{},{}]],
                    subplot_titles=("ODM", "ADS")
                    )
fig.add_trace(fig1, row=1, col=1)
fig.add_trace(fig2, row=1, col=2)

fig.update_layout(
    barmode='stack', 
    title={'text': f"creditScore vs Income",
          'x':0.5,
          'xanchor': 'center'
    })
"""

fig1.update_xaxes(title_text='Yearly income')
fig1.update_yaxes(title_text='Loan amount')

fig1.update_layout(
    barmode='stack', 
    showlegend=False,
    title={'text': f"ODM : Behaviours according to income and loan amounts",
          'x':0.5,
          'xanchor': 'center'
    })


fig2.update_xaxes(title_text='Yearly income')
fig2.update_yaxes(title_text='Loan amount')

fig2.update_layout(
    barmode='stack', 
    showlegend=False,
    title={'text': f"ADS : Behaviours according to income and loan amounts",
          'x':0.5,
          'xanchor': 'center'
    })

iplot(fig1)
iplot(fig2)

In [14]:
############ SCATTER CHART #############
max_marker_size = 10
trace_scatter_odm = go.Scatter(
                 x=datasink_odm[get_decision_borrower_yearly_income_odm],
                 y=datasink_odm[get_decision_borrower_credit_score_odm],
                 mode='markers',
                 marker_size=array_normalize(datasink_odm[get_decision_amount_odm], max_marker_size), 
                 marker_color=set_colors(datasink_odm[get_decision_approval_odm]),
                 text=datasink_ads[get_decision_approval_ads], 
                 hovertemplate="<b>Income:</b> %{x}<br><b>creditScore:</b> %{y}<br><b>Approval:</b> %{text}<extra></extra>",
                 name='ODM'
)

trace_scatter_ads = go.Scatter(
                 x=datasink_ads[get_decision_borrower_yearly_income_ads],
                 y=datasink_ads[get_decision_borrower_credit_score_ads],
                 mode='markers',
                 marker_size=array_normalize(datasink_ads[get_decision_amount_ads], max_marker_size), 
                 marker_color=set_colors(datasink_ads[get_decision_approval_ads]),
                 text=datasink_ads[get_decision_approval_ads], 
                 hovertemplate="<b>Income:</b> %{x}<br><b>creditScore:</b> %{y}<br><b>Approval:</b> %{text}<extra></extra>",
                 name='ADS',
)

fig = make_subplots(rows=1, cols=2,
                    specs=[[{"type": "scatter"},{"type": "scatter"}]],
                    subplot_titles=("ODM", "ADS")
                    )
fig.add_trace(trace_scatter_odm, row=1, col=1)
fig.add_trace(trace_scatter_ads, row=1, col=2)

fig.update_xaxes(title_text='Yearly income')
fig.update_yaxes(title_text='Credit score')

fig.update_layout(
    barmode='stack', 
    showlegend=False,
    title={'text': f"creditScore vs Income",
          'x':0.5,
          'xanchor': 'center'
    })

iplot(fig)

__BIDIRECTIONAL BAR CHARTS__

In [15]:
fig = make_subplots(rows=4, cols=2, specs=[[{}, {}], [{}, {}], [{}, {}], [{}, {}]], shared_xaxes=False,
                    shared_yaxes=True, horizontal_spacing=0)

rejected_loan=[datasink_odm.query(select_rejected_decision_odm).shape[0], datasink_ads.query(select_rejected_decision_ads).shape[0]]
rejected_loan_amount=[datasink_odm.query(select_rejected_decision_odm)[get_decision_amount_odm].sum(), datasink_ads.query(select_rejected_decision_ads)[get_decision_amount_ads].sum()]
approved_loan=[datasink_odm.query(select_approved_decision_odm).shape[0], datasink_ads.query(select_approved_decision_ads).shape[0]]
approved_loan_amount=[datasink_odm.query(select_approved_decision_odm)[get_decision_amount_odm].sum(), datasink_ads.query(select_approved_decision_ads)[get_decision_amount_ads].sum()]


fig.append_trace(go.Bar(
    y=['number of rejected applications'],
    x=[rejected_loan[0]],
    name='Rejected',
    text=rejected_loan[0],
    textposition='inside',
    showlegend=False,
    marker_color='#4472c4',
    #base=0,
    orientation='h',
), 1, 1)
fig.append_trace(go.Bar(
    y=['number of rejected applications'],
    x=[rejected_loan[1]],
    name='Rejected',
    text=rejected_loan[1],
    #base=0,
    textposition='inside',
    showlegend=False,
    orientation='h',
    marker_color='#ed7d31'
), 1, 2)


fig.append_trace(go.Bar(
    y=['sum of rejected applications amounts'],
    x=[rejected_loan_amount[0]],
    name='Rejected',
    text=str(rejected_loan_amount[0]),
    textposition='inside',
    showlegend=False,
    marker_color='#4472c4',
    #base=0,
    orientation='h',
), 2, 1)
fig.append_trace(go.Bar(
    y=['sum of rejected applications amounts'],
    x=[rejected_loan_amount[1]],
    name='Rejected',
    text=str(rejected_loan_amount[1]),
    #base=0,
    textposition='inside',
    showlegend=False,
    orientation='h',
    marker_color='#ed7d31'
), 2, 2)


fig.append_trace(go.Bar(
    y=['number of approved applications'],
    x=[approved_loan[0]],
    name='Approved',
    text=approved_loan[0],
    textposition='inside',
    showlegend=False,
    marker_color='#4472c4',
    #base=0,
    orientation='h',
), 3, 1)
fig.append_trace(go.Bar(
    y=['number of approved applications'],
    x=[approved_loan[1]],
    name='Approved',
    text=approved_loan[1],
    #base=0,
    textposition='inside',
    showlegend=False,
    orientation='h',
    marker_color='#ed7d31'
), 3, 2)

fig.append_trace(go.Bar(
    y=['sum of approved applications amounts'],
    x=[approved_loan_amount[0]],
    name='Approved',
    text=str(approved_loan_amount[0]),
    textposition='inside',
    showlegend=False,
    marker_color='#4472c4',
    #base=0,
    orientation='h',
), 4, 1)
fig.append_trace(go.Bar(
    y=['sum of approved applications amounts'],
    x=[approved_loan_amount[1]],
    name='Approved',
    text=str(approved_loan_amount[1]),
    #base=0,
    textposition='inside',
    showlegend=False,
    orientation='h',
    marker_color='#ed7d31'
), 4, 2)

butterfly_amount_view_width_ratio = max([datasink_ads.query(select_rejected_decision_ads)[get_decision_amount_ads].sum(),
                                        datasink_ads.query(select_approved_decision_ads)[get_decision_amount_ads].sum(),
                                        datasink_odm.query(select_rejected_decision_odm)[get_decision_amount_ads].sum(),
                                        datasink_odm.query(select_approved_decision_odm)[get_decision_amount_ads].sum()]) * 1.2

butterfly_approval_view_width_ratio = max([datasink_ads.query(select_rejected_decision_ads).shape[0],
                                        datasink_ads.query(select_approved_decision_ads).shape[0],
                                        datasink_odm.query(select_rejected_decision_odm).shape[0],
                                        datasink_odm.query(select_approved_decision_odm).shape[0]]) * 1.2

fig.update_xaxes(showticklabels=True, row=1, col=1, range=[butterfly_approval_view_width_ratio, 0])
fig.update_xaxes(showticklabels=True, row=1, col=2, range=[0, butterfly_approval_view_width_ratio])

fig.update_xaxes(showticklabels=True, row=2, col=1, range=[butterfly_amount_view_width_ratio, 0])
fig.update_xaxes(showticklabels=True, row=2, col=2, range=[0, butterfly_amount_view_width_ratio])

fig.update_xaxes(showticklabels=True, row=3, col=1, range=[butterfly_approval_view_width_ratio, 0])
fig.update_xaxes(showticklabels=True, row=3, col=2, range=[0, butterfly_approval_view_width_ratio])

fig.update_xaxes(showticklabels=True, title_text="ODM", row=4, col=1, range=[butterfly_amount_view_width_ratio, 0])
fig.update_xaxes(showticklabels=True, title_text="ADS", row=4, col=2, range=[0, butterfly_amount_view_width_ratio])


fig.update_layout(
    barmode='stack',
    height=800,
    title={'text': f"Runs comparison",
          'x':0.55,
          'xanchor': 'center'
    })

"""
fig.update_yaxes(
        ticktext=bidirectional_bar_chart_label,
        tickvals=bidirectional_bar_chart_label
    )
"""

iplot(fig)

__RADAR CHART__

In [16]:
fig = go.Figure()

#radar dimension normalization 
radar_max_value = 5
values = np.array([[rejected_loan[0], rejected_loan_amount[0], approved_loan[0], approved_loan_amount[0], approved_loan[0]/(approved_loan[0]+rejected_loan[0])],
                   [rejected_loan[1], rejected_loan_amount[1], approved_loan[1], approved_loan_amount[1], approved_loan[1]/(approved_loan[1]+rejected_loan[1])]])
normed_values = (values*radar_max_value) / values.max(axis=0)

def radar_normalization(values, max_value):
    normalized_values = []
    for value in values:
        normalized_values.append((value*max_value)/max(values))
    return normalized_values

fig.add_trace(go.Scatterpolar(
      r=normed_values[0],
      theta=radar_chart_labels,
      fill='toself',
      name='ODM',
))
fig.add_trace(go.Scatterpolar(
      r=normed_values[1],
      theta=radar_chart_labels,
      fill='toself',
      name='ADS'
))

fig.update_layout(
  polar=dict(
    bgcolor= 'black',
    radialaxis=dict(
      visible=True,
      range=[0, radar_max_value],
      #gridcolor='red',
      #axiscolor='red',
      #tickcolor='red',
    )),
  #showlegend=False
)

fig.show()

__VIOLIN PLOT__

__VIOLIN FIRST VARIANT__ FOR LOAN AMOUNT

In [17]:
subplot_titles = ['ODM approved', 'ADS approved', 'ODM rejected', 'ADS rejected']
select_decision_approval_status = [select_approved_decision_odm, select_approved_decision_ads, select_rejected_decision_odm, select_rejected_decision_ads]
datasink =[datasink_odm, datasink_ads, datasink_odm, datasink_ads]
get_decision_value = [get_decision_amount_odm, get_decision_amount_ads, get_decision_amount_odm, get_decision_amount_ads] # Y value 

fig = go.Figure()
for idx, approval in enumerate(select_decision_approval_status):
    fig.add_trace(go.Violin(y=datasink[idx].query(approval)[get_decision_value[idx]],
                            name=subplot_titles[idx],
                            box_visible=True,
                            meanline_visible=True,
                            points='all'
                            ))

fig.update_yaxes(title_text='Loan amount')

fig.update_layout(
    barmode='stack', 
    showlegend=False,
    title={'text': f"Loan amount according to approval status : ODM vs ADS",
          'x':0.5,
          'xanchor': 'center'
    })

fig.show()

__VIOLIN SECOND VARIANT__ FOR LOAN AMOUNT

In [18]:
subplot_titles = ['ODM/ADS approved', 'ODM/ADS rejected']
select_decision_approval_status = [select_approved_decision_odm, select_rejected_decision_odm, select_approved_decision_ads, select_rejected_decision_ads]
datasink =[datasink_odm, datasink_ads]

fig = go.Figure()
for idx in range(0,2):
    fig.add_trace(go.Violin(y=datasink_odm.query(select_decision_approval_status[idx])[get_decision_amount_odm],
                            name=subplot_titles[idx],
                            legendgroup=subplot_titles[idx], scalegroup=subplot_titles[idx],
                            side='negative',
                            line_color='blue')
                )
    fig.add_trace(go.Violin(y=datasink_ads.query(select_decision_approval_status[idx+2])[get_decision_amount_ads],
                            name=subplot_titles[idx],
                            legendgroup=subplot_titles[idx], scalegroup=subplot_titles[idx],
                            side='positive',
                            line_color='orange')
                )

fig.update_traces(meanline_visible=True)
fig.update_layout(violingap=0, violinmode='overlay')
fig.update_yaxes(title_text='Loan amount')

fig.update_layout(
    barmode='stack', 
    showlegend=False,
    title={'text': f"Loan amount according to approval status : ODM vs ADS",
          'x':0.5,
          'xanchor': 'center'
    })
fig.show()

__VIOLIN VARIANT FOR CREDIT SCORE__

In [19]:
subplot_titles = ['ODM approved', 'ADS approved', 'ODM rejected', 'ADS rejected']
select_decision_approval_status = [select_approved_decision_odm, select_approved_decision_ads, select_rejected_decision_odm, select_rejected_decision_ads]
datasink =[datasink_odm, datasink_ads, datasink_odm, datasink_ads]
get_decision_value = [get_decision_borrower_credit_score_odm, get_decision_borrower_credit_score_ads, get_decision_borrower_credit_score_odm, get_decision_borrower_credit_score_ads] # Y value 

fig = go.Figure()
for idx, approval in enumerate(select_decision_approval_status):
    fig.add_trace(go.Violin(y=datasink[idx].query(approval)[get_decision_value[idx]],
                            name=subplot_titles[idx],
                            box_visible=True,
                            meanline_visible=True,
                            points='all'
                            ))

fig.update_yaxes(title_text='Credit score')

fig.update_layout(
    barmode='stack', 
    showlegend=False,
    title={'text': f"Credit score according to approval status : ODM vs ADS",
          'x':0.5,
          'xanchor': 'center'
    })

fig.show()

__LOAN REQUEST MAPBOX__

In [20]:
mapbox_access_token = "pk.eyJ1IjoiZGVtYmVsZXQiLCJhIjoiY2t0Mm5oeWo4MGx6ODJ3cXAwejNtMTFncCJ9.9cyxovpJjJUINMrw4ofe_g"

nomi = pgeocode.Nominatim('us')
df=nomi.query_postal_code(datasink_ads[get_decision_borrower_zipcode_ads].values)

fig = go.Figure(data=go.Scattermapbox(
        lon = df['longitude'],
        lat = df['latitude'],
        text = df['place_name'],
        mode = 'markers',
        marker=go.scattermapbox.Marker(
            size=array_normalize(datasink_ads[get_decision_borrower_credit_score_ads], 20),
            color=set_colors(datasink_ads[get_decision_approval_ads])
        ),
        ))

fig.update_layout(
    title='ADS : Loan requests localisation',
    autosize=True,
    hovermode='closest',
    showlegend=False,
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=df['latitude'].mean(),
            lon=df['longitude'].mean()
        ),
        pitch=0,
        zoom=3,
        style='light'
    ),
)
fig.show()

__LOAN REQUEST MAP__

In [21]:
nomi = pgeocode.Nominatim('us')
df=nomi.query_postal_code(datasink_ads[get_decision_borrower_zipcode_ads].values)

fig = go.Figure(data=go.Scattergeo(
        lon = df['longitude'],
        lat = df['latitude'],
        text = df['place_name'],
        mode = 'markers',
        marker_size=array_normalize(datasink_ads[get_decision_borrower_credit_score_ads], 20),
        marker_color=set_colors(datasink_ads[get_decision_approval_ads])
        ))

fig.update_layout(
        title = 'ADS : Loan requests localisation',
        geo_scope='usa',
    )
fig.show()